# Damaged induced traps

In [1]:
import numpy as np
import festim as F
import h_transport_materials as htm

D = htm.diffusivities.filter(material="tungsten").filter(author="frauenfelder")[0]

# common values
atom_density_W = 6.3222e28
minute = 60
day = minute * 60 * 24
week = day * 7
fpy = day * 365
dpa = 5

my_model = F.Simulation(log_level=40)

# define materials
tungsten = F.Material(D_0=D.pre_exp.magnitude, E_D=D.act_energy.magnitude, id=1)
my_model.materials = tungsten


# define traps
lambda_val = 1.1e-10  # m
trap_W_1 = F.Trap(
    k_0=tungsten.D_0 / (lambda_val**2 * 6 * atom_density_W),
    E_k=tungsten.E_D,
    p_0=1e13,
    E_p=1.04,
    density=2.4e22,
    materials=tungsten,
)
trap_W_damage_4 = F.NeutronInducedTrap(
    k_0=tungsten.D_0 / (lambda_val**2 * 6 * atom_density_W),
    E_k=tungsten.E_D,
    p_0=1e13,
    E_p=1.85,
    A_0=6.1838e-03,
    E_A=0.30,
    phi=dpa / fpy,
    K=5.0e26,
    n_max=4.7e25,
    materials=tungsten,
)

my_model.traps = [trap_W_1, trap_W_damage_4]

vertices = np.linspace(0, 2e-03, num=1000)
my_model.mesh = F.MeshFromVertices(vertices)

# define temperature
my_model.T = 800

# define boundary conditions
my_model.boundary_conditions = [
    F.ImplantationDirichlet(
        surfaces=1,
        phi=1e20,
        R_p=3e-09,
        D_0=tungsten.D_0,
        E_D=tungsten.E_D,
    ),
]

# define exports
results_folder = "task17/"
my_derived_quantities = F.DerivedQuantities(
    [F.TotalVolume("solute", volume=1)],
    show_units=True,
)
my_model.exports = [
    F.TXTExport(
        field="retention",
        filename=results_folder + "retention_profile.txt",
    ),
    my_derived_quantities,
]

# define settings
my_model.dt = F.Stepsize(
    initial_value=0.1,
    stepsize_change_ratio=1.1,
    dt_min=1e-1,
)
my_model.settings = F.Settings(
    transient=True,
    final_time=fpy,
    absolute_tolerance=1e10,
    relative_tolerance=1e-10,
)

# run simulation
my_model.initialise()
my_model.run()

Defining initial values
Defining variational problem
Defining source terms
Defining boundary conditions
Time stepping...
100.0 %        3.2e+07 s    Elapsed time so far: 43.6 s


In [2]:
my_standard_model = my_model

my_standard_model.traps = [trap_W_1]
my_standard_model.exports = [
    F.TXTExport(
        field="retention",
        filename=results_folder + "retention_profile_standard.txt",
    ),
    my_derived_quantities,
]
my_standard_model.initialise()
my_standard_model.run()

Defining initial values
Defining variational problem
Defining source terms
Defining boundary conditions
Time stepping...
100.0 %        3.2e+07 s    Elapsed time so far: 32.3 s


In [3]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from IPython.display import HTML

results_folder = "task17/"
data_damaged = np.genfromtxt(
    results_folder + "retention_profile.txt", delimiter=",", skip_header=1
)
data_standard = np.genfromtxt(
    results_folder + "retention_profile_standard.txt", delimiter=",", skip_header=1
)
times = my_derived_quantities.t

# # Separate the x values and y values for each time step
x_damaged, y_damaged = data_damaged[:, 0] * 1e3, data_damaged[:, 1:]
x_standard, y_standard = data_standard[:, 0] * 1e3, data_standard[:, 1:]

# Set up the figure and axis
fig, ax = plt.subplots()
(line1,) = ax.plot([], [], lw=2, color="red", label="damaged")
(line2,) = ax.plot([], [], lw=2, color="black", label="standard")


# Initialization function to set up the background of each frame
def init():
    line1.set_data([], [])
    line2.set_data([], [])
    ax.set_xlim(0, 2)
    ax.set_ylim(1e14, 1e26)
    ax.set_yscale("log")
    ax.legend()
    ax.set_xlabel(r"x (mm)")
    ax.set_ylabel(r"T retention (m$^{-3}$)")
    ax.spines["top"].set_visible(False)
    ax.spines["right"].set_visible(False)

    return line1, line2


def animate(i):
    y1 = y_damaged[:, i]
    y2 = y_standard[:, i]
    line1.set_data(x_damaged, y1)
    line2.set_data(x_standard, y2)
    one_min, one_hour, one_day = 60, 3600, 3600 * 24
    t = times[i]  # NOTE this only works because both models have the same timesteps
    if t < one_min:
        ax.set_title(f"Time: {t:.1f} seconds")
    elif t < one_hour:
        ax.set_title(f"Time: {t/one_min:.1f} minutes")
    elif t < one_day:
        ax.set_title(f"Time: {t/one_hour:.1f} hours")
    else:
        ax.set_title(f"Time: {t/one_day:.1f} days")
    return line1, line2


# Call the animator
ani = animation.FuncAnimation(
    fig, animate, init_func=init, frames=y_damaged.shape[1], interval=50, blit=True
)

plt.close(fig)

# Display the animation in the Jupyter Notebook
HTML(ani.to_jshtml())